# Vans-and-Drones System for Last-Mile Delivery


Definition of Network:
- $G$ is a directed grapf, with $G=(V,E)$
- $n$ is total number of customers
- $V$ is set of customer nodes, $V=\{0,1,...,n\}$, with $V=\{0\}$ representing the depot
- $E$ is the set of arcs (edges), $E=\{(i,j)\in V^2 : i\neq j\}$ that connects each node pair $e_{ij}=(i,j)$
- $K$ is total number of trucks, with $K=\{1,2,...,k\}$
- $KD$ is total number of drones, with $KD=\{1,2,...,kd\}$
- $c^k_{ij}$ is truck travel cost over arc $(i,j)\in E: j\neq i$ (represented with distance between i and j)
- $c^{kd}_{ij}$ is drone travel cost over arc $(i,j)\in E: j\neq i$ (represented with distance between i and j)
- $Q_t \geq 0$ is total truck capacity, equal for all trucks in $K$
- $Q_d \geq 0$ is total drone capacity, equal for all drones in $KD$
- $q_i \geq 0$ is demand at node $i\in V$, demand at depot $V\{0\}=0$

Definition of decision variables:
- $x^k_{ij}=1$ if truck travels along arc $e_{ij}$, else 0
- $x^{kd}_{ij}=1$ if drone travels along arc $e_{ij}$, else 0

Mathematical Formulation:
$$\begin{align}
\min \quad & \sum_{k\in K} \sum_{(i,j)\in E} c^k_{ij} x^k_{ij} + \sum_{kd\in KD} \sum_{(i,j)\in E} c^{kd}_{ij} x^{kd}_{ij} && && \quad \text{(1)}\\
\text{subject to} \quad & \sum_{k\in K} \sum_{i\in V, i\neq j} x^k_{ij} + \sum_{kd\in KD} \sum_{i\in V, i\neq j} x^{kd}_{ij} = 1 && \forall j \in V\setminus \{0\} && \quad \text{(2)}\\
& \sum_{j\in V\setminus \{0\}} x^k_{0j} = 1 && \forall k\in K && \quad \text{(3)}\\
& \sum_{j\in V\setminus \{0\}} x^{kd}_{0j} = 1 && \forall kd\in KD && \quad \text{(4)}\\
& \sum_{i\in V\setminus \{0\}} x^k_{i0} = 1 && \forall k\in K && \quad \text{(5)}\\
& \sum_{i\in V\setminus \{0\}} x^{kd}_{i0} = 1 && \forall kd\in KD && \quad \text{(6)}\\
& \sum_{i\in V, i\neq j} x^k_{ij} + \sum_{i\in V, i\neq j} x^{kd}_{ij} - \sum_{i\in V} x^k_{ji} + \sum_{i\in V} x^{kd}_{ji} = 0 && \forall j\in V, \forall k\in K, \forall kd\in KD && \quad \text{(7)}\\
& \sum_{i\in V} \sum_{j\in V\setminus \{0\},i\neq j} q_j x^k_{ij} \leq Q_k && \forall k\in K && \quad \text{(8)}\\
& \sum_{i\in V} \sum_{j\in V\setminus \{0\},i\neq j} q_j x^{kd}_{ij} \leq Q_{kd} && \forall kd\in KD && \quad \text{(9)}\\
& \sum_{k\in K} \sum_{(i,j)\in S, i\neq j} x^k_{ij}\leq |S|-r(s) && S\subseteq V\setminus \{0\} && \quad \text{(10)}\\
& \sum_{kd\in KD} \sum_{(i,j)\in S, i\neq j} x^{kd}_{ij}\leq |S|-r(s) && S\subseteq V\setminus \{0\} && \quad \text{(11)}\\
& \\
& x^k_{ij}\in \{0,1\} && \forall (i,j)\in E, \quad\forall k\in K && \quad \text{(12)}\\
& x^{kd}_{ij}\in \{0,1\} && \forall (i,j)\in E, \quad\forall kd\in KD && \quad \text{(13)}\\
\end{align}$$

In [ ]:
import numpy as np
import pandas as pd
import cplex
import gmaps
import googlemaps
import pulp
import itertools

API_KEY = ''
gmaps.configure(api_key=API_KEY)
googlemaps = googlemaps.Client(key=API_KEY)

customers = 
trucks = 
truck_capacity = 
drones = 
drone_capacity = 
fixed_cost_truck = 

depot_lat =  
depot_long = 
np.random.seed(0)
df = pd.DataFrame({"lat":np.random.logistic(depot_lat, 0.002, customers), 
                   "long":np.random.logistic(depot_long, 0.002, customers), 
                   "demand":np.random.randint(1, 10, customers)})
df.iloc[0,0] = depot_lat
df.iloc[0,1] = depot_long
df.iloc[0,2] = 0

print(df)


In [ ]:
pd.options.mode.chained_assignment = None 
# Retrieve Distance Matrix Trucks
def _distance_matrix_truck(_df):
    # Create empty matrix
    _travel_distance_truck = np.zeros((len(_df),len(_df)))
    _df['lat-long'] = '0'
    for i in range(len(_df)):
        _df['lat-long'].iloc[i] = str(_df.lat[i]) + ',' + str(_df.long[i])
    
    for i in range(len(_df)):
        for j in range(len(_df)):
            
            # Retrieve distances between customer nodes
            _gmaps_results = googlemaps.directions(_df['lat-long'].iloc[i],
                                                            _df['lat-long'].iloc[j],
                                                            mode = 'driving')
            # Append distances to matrix
            _travel_distance_truck[i][j] = _gmaps_results[0]['legs'][0]['distance']['value']
            
    return _travel_distance_truck

distance_truck = _distance_matrix_truck(df)

print(distance_truck)


In [ ]:
pd.options.mode.chained_assignment = None 
from haversine import haversine, Unit
#Retrieve Distance Matrix Drones
def _distance_matrix_drone(_df):
    
    _travel_distance_drone = np.zeros((len(_df),len(_df)))
    _df['lat-long'] = '0'
    for i in range(len(_df)):
        _df['lat-long'].iloc[i] = (df.lat[i],df.long[i])                                    
                                           
    for i in range(len(_df)):
        for j in range(len(_df)):
            # Calculate distances between customer nodes
            _haversine_result = haversine(_df['lat-long'].iloc[i],
                                          _df['lat-long'].iloc[j],
                                          unit='m')
            
            # Append distances to matrix
            _travel_distance_drone[i][j] = int(_haversine_result)
            
    return _travel_distance_drone

distance_drone = _distance_matrix_drone(df)

print(distance_drone)

In [ ]:
import matplotlib.pyplot as plt
plt.figure(figsize=(8,8))
ax=plt.axes()
ax.set_facecolor('aliceblue')
for i in range(customers):
    if i == 0:
        plt.scatter(df.lat[i], df.long[i], marker='s', c='black', s=200)
        plt.text(df.lat[i]-0.00095, df.long[i], "Depot", fontsize=14)
    else:
        plt.scatter(df.lat[i], df.long[i], c='red', s=50)
        plt.text((df.lat[i]+0.0001), df.long[i], ('$q_%d=%d$'%((i,df.demand[i]))),
                 fontsize=14)

In [ ]:
def _customer_plot(_df):
    
    _customer_locations = []
    for i in range(1,len(_df)):
        _customer_locations.append((_df['lat'].iloc[i],_df['long'].iloc[i]))
    
    _fig = gmaps.figure()
    _pins = gmaps.marker_layer(_customer_locations)  
    _fig.add_layer(_pins)
    _depot_location=[]
    for i in range(0,1):
        _depot_location.append((_df['lat'].iloc[0],_df['long'].iloc[0]))
    _depot = gmaps.symbol_layer(_depot_location,fill_color='black', scale=6)
    _fig.add_layer(_depot)
    
    return _fig
customer_plt = _customer_plot(df)
customer_plt

In [ ]:
from pulp import *
# Vans-and-Drones Routing Model
for trucks in range(1,trucks+1):

    prob = LpProblem("VRPD", LpMinimize)

    # Define decision variables for truck and drone
    xt = [[[LpVariable("xt%s_%s,%s"%(i,j,k), cat="Binary") if i != j else None 
            for k in range(trucks)]for j in range(customers)] for i in range(customers)]
    xd = [[[LpVariable("xd%s_%s,%s"%(i,j,kd), cat="Binary") if i != j else None
            for kd in range(drones)]for j in range(customers)] for i in range(customers)]

    # Objective function - Minimize total travel cost
    prob += lpSum((distance_truck[i][j] * xt[i][j][k]) if i != j else 0
                        for k in range(trucks)
                        for j in range(customers)
                        for i in range (customers)) + lpSum((fixed_cost_truck * xt[0][j][k])
                                                            for k in range(trucks)
                                                            for j in range(1,customers)) + lpSum((distance_drone[i][j] * xd[i][j][kd] if i!=j else 0
                                                                                                  for kd in range(drones)
                                                                                                  for j in range(customers)
                                                                                                  for i in range(customers)))

    # Constraint 1 - Customer is only served once by only one vehicle
    for j in range(1, customers):
        prob += lpSum(xt[i][j][k] if i != j else 0
                      for i in range(customers)
                      for k in range(trucks)) + lpSum(xd[i][j][kd] if i != j else 0
                                                      for i in range(customers)
                                                      for kd in range(drones)) == 1 

    # Constraint 2 - Vehicle must depart from and return to depot
    for k in range(trucks):
        prob += lpSum(xt[0][j][k] for j in range(1,customers)) == 1
        prob += lpSum(xt[i][0][k] for i in range(1,customers)) == 1

    for kd in range(drones):
        prob += lpSum(xd[0][j][kd] for j in range(1,customers)) == 1
        prob += lpSum(xd[i][0][kd] for i in range(1,customers)) == 1

    # Constraint 3 - Only one vehicle enters and leaves each customer location
    for k in range(trucks):
        for kd in range(drones):
            for j in range(customers):
                prob += (lpSum(xt[i][j][k] if i != j else 0
                               for i in range(customers)) + lpSum(xd[i][j][kd] if i!=j else 0
                                                                  for i in range(customers))) - (lpSum(xt[j][i][k] 
                                                                                                       for i in range(customers)) + lpSum(xd[j][i][kd] 
                                                                                                                                          for i in range(customers))) == 0

    # Constraint 4 - Demand must not exceed vehicle capacity
    for k in range(trucks):
        prob += lpSum(df.demand[j] * xt[i][j][k] if i != j else 0 
                      for i in range(customers) for j in range (1,customers)) <= truck_capacity
    for kd in range(drones):
        prob += lpSum(df.demand[j] * xd[i][j][kd] if i != j else 0 
                      for i in range(customers) for j in range (1,customers)) <= drone_capacity

    # Constraint 5 - Subtour elimination
    subtours = []
    for i in range(2,customers):
        subtours += itertools.combinations(range(1,customers), i)

    for s in subtours:
        prob += lpSum(xt[i][j][k] if i !=j else 0 for i, j in itertools.permutations(s,2) 
                      for k in range(trucks)) <= len(s) - 1

    for s in subtours:
        prob += lpSum(xd[i][j][kd] if i !=j else 0 for i, j in itertools.permutations(s,2) 
                      for kd in range(drones)) <= len(s) - 1

    if prob.solve(CPLEX_PY()) == 1:
        prob.writeLP("VRPDModel.lp")
    #for v in prob.variables():
        #print(v.name, "=", v.varValue)
        print('Status:', LpStatus[prob.status])
        print('Trucks:', trucks)
        print('Drones:', drones)
        print('Total distance traveled:', pulp.value(prob.objective))
        break

In [ ]:
plt.figure(figsize=(8,8))
ax=plt.axes()
ax.set_facecolor('aliceblue')
for i in range(customers):    
    if i == 0:
        plt.scatter(df.lat[i], df.long[i], c='black', marker='s', s=200)
        plt.text(df.lat[i]-0.001, df.long[i], "Depot", fontsize=16)
    else:
        plt.scatter(df.lat[i], df.long[i], c='red', s=100)
        plt.text((df.lat[i]+0.0001), df.long[i], ('$q_%d=%d$'%((i,df.demand[i]))), fontsize=14)
color_list = ["red","blue","green","yellow"]
for k in range(trucks): 
    for i in range(customers):
        for j in range(customers):
            if i != j and pulp.value(xt[i][j][k]) == 1:
                plt.arrow(df.lat[i], df.long[i], (df.lat[j] - df.lat[i]), (df.long[j] - df.long[i]),
                          width=0.00001, head_width=0.0002, color=color_list[k], length_includes_head=True)

color_list_d = ["purple","white"]                
for kd in range(drones): 
    for i in range(customers):
        for j in range(customers):
            if i != j and pulp.value(xd[i][j][kd]) == 1:
                plt.arrow(df.lat[i], df.long[i], (df.lat[j] - df.lat[i]), (df.long[j] - df.long[i]),
                          width=0.00001,length_includes_head=True, head_width=0.0002, color=color_list_d[kd],
                          linestyle='dotted')

In [ ]:
fig = gmaps.figure()
layer_truck = []
color_truck = ["red","blue","green","black"]

for k in range(trucks):
    for i in range(customers):
        for j in range(customers):
            if i != j and pulp.value(xt[i][j][k]) == 1:
                layer_truck.append(gmaps.directions.Directions(
                    (df.lat[i],df.long[i]),
                    (df.lat[j],df.long[j]),
                    mode='car',stroke_color=color_truck[k],stroke_opacity=1.0, stroke_weight=5.0))

for i in range(len(layer_truck)):
    fig.add_layer(layer_truck[i])

layer_drone = []
color_drone = ["purple","yellow"]
for kd in range(drones):
    for i in range(customers):
        for j in range(customers):
            if i != j and pulp.value(xd[i][j][kd]) == 1:
                drawing=(gmaps.Line(start=(df.lat[i], df.long[i]), end=(df.lat[j], df.long[j]),
                             stroke_color=color_drone[kd],stroke_opacity=1.0, stroke_weight=5.0))              
                mark=(gmaps.Marker((df.lat[i],df.long[i])))

                layer_drone_draw = gmaps.drawing_layer(features=[mark, drawing])
                layer_drone.append(layer_drone_draw)
for i in range(len(layer_drone)):
    fig.add_layer(layer_drone[i])
    
depot_location=[]
for i in range(0,1):
    depot_location.append((df['lat'].iloc[0],df['long'].iloc[0]))
    depot = gmaps.symbol_layer(depot_location,fill_color='black', stroke_color='black', scale=6)
    fig.add_layer(depot)

                
fig